* https://towardsdatascience.com/hyperparameter-optimization-in-python-part-0-introduction-c4b66791614b
* https://github.com/neptune-ai/blog-hyperparameter_optimization

In [1]:
import lightgbm as lgb
from sklearn.model_selection import train_test_split

In [2]:
NUM_BOOST_ROUND = 300
EARLY_STOPPING_ROUNDS = 30

In [3]:
def train_evaluate(X, y, params):
    X_train, X_valid, y_train, y_valid = train_test_split(X, y, 
                                                          test_size=0.2, 
                                                          random_state=47)

    train_data = lgb.Dataset(X_train, label=y_train)
    valid_data = lgb.Dataset(X_valid, label=y_valid, reference=train_data)

    model = lgb.train(params, train_data,
                      num_boost_round=NUM_BOOST_ROUND,
                      early_stopping_rounds=EARLY_STOPPING_ROUNDS,
                      valid_sets=[valid_data], 
                      valid_names=['valid'])
    
    score = model.best_score['valid']['auc']
    return score

In [4]:
import pandas as pd

N_ROWS=10000
TRAIN_PATH = 'data/TRAIN.csv'

data = pd.read_csv(TRAIN_PATH, nrows=N_ROWS)
X = data.drop(['ID_code', 'target'], axis=1)
y = data['target']
    
MODEL_PARAMS = {'boosting': 'gbdt',
                'objective':'binary',
                'metric': 'auc',
                'num_threads': 12,
                'learning_rate': 0.3,
                }

score = train_evaluate(X, y, MODEL_PARAMS)
print('Validation AUC: {}'.format(score))

[1]	valid's auc: 0.610001
Training until validation scores don't improve for 30 rounds
[2]	valid's auc: 0.645257
[3]	valid's auc: 0.654526
[4]	valid's auc: 0.668272
[5]	valid's auc: 0.678362
[6]	valid's auc: 0.691811
[7]	valid's auc: 0.691745
[8]	valid's auc: 0.699368
[9]	valid's auc: 0.710054
[10]	valid's auc: 0.709166
[11]	valid's auc: 0.711269
[12]	valid's auc: 0.716855
[13]	valid's auc: 0.718082
[14]	valid's auc: 0.715187
[15]	valid's auc: 0.718826
[16]	valid's auc: 0.724149
[17]	valid's auc: 0.728786
[18]	valid's auc: 0.732322
[19]	valid's auc: 0.733539
[20]	valid's auc: 0.734347
[21]	valid's auc: 0.733298
[22]	valid's auc: 0.734718
[23]	valid's auc: 0.738281
[24]	valid's auc: 0.740828
[25]	valid's auc: 0.741148
[26]	valid's auc: 0.746637
[27]	valid's auc: 0.747693
[28]	valid's auc: 0.747823
[29]	valid's auc: 0.747828
[30]	valid's auc: 0.752556
[31]	valid's auc: 0.751442
[32]	valid's auc: 0.751324
[33]	valid's auc: 0.753154
[34]	valid's auc: 0.754516
[35]	valid's auc: 0.755475
[36

In [6]:
def objective(params):
    all_params = {**params, **STATIC_PARAMS}
    return -1.0 * train_evaluate(X, y, all_params)

In [11]:
from hyperopt import hp, fmin, tpe, hp, STATUS_OK, Trials
from collections import OrderedDict
import numpy as np

HPO_PARAMS = {'max_evals': 100,}
STATIC_PARAMS = {'boosting': 'gbdt',
                 'objective': 'binary',
                 'metric': 'auc',
                 'num_threads': 12,
                 }

SPACE = OrderedDict([('learning_rate', hp.loguniform('learning_rate', np.log(0.01), np.log(0.5))),
                    ('max_depth', hp.choice('max_depth', range(1, 30, 1))),
                    ('num_leaves', hp.choice('num_leaves', range(2, 100, 1))),
                    ('min_data_in_leaf', hp.choice('min_data_in_leaf', range(10, 1000, 1))),
                    ('feature_fraction', hp.uniform('feature_fraction', 0.1, 1.0)),
                    ('subsample', hp.uniform('subsample', 0.1, 1.0))
                    ])
trials = Trials()
_ = fmin(objective, SPACE, trials=trials, algo=tpe.suggest, **HPO_PARAMS)

[1]	valid's auc: 0.650251                                                                                                                                                    
Training until validation scores don't improve for 30 rounds                                                                                                                 
[2]	valid's auc: 0.689792                                                                                                                                                    
[3]	valid's auc: 0.692417                                                                                                                                                    
[4]	valid's auc: 0.702519                                                                                                                                                    
[5]	valid's auc: 0.715001                                                                                                         

[47]	valid's auc: 0.780044                                                                                                                                                   
[48]	valid's auc: 0.780229                                                                                                                                                   
[49]	valid's auc: 0.781589                                                                                                                                                   
[50]	valid's auc: 0.783607                                                                                                                                                   
[51]	valid's auc: 0.786464                                                                                                                                                   
[52]	valid's auc: 0.785232                                                                                                        

[94]	valid's auc: 0.804184                                                                                                                                                   
[95]	valid's auc: 0.804444                                                                                                                                                   
[96]	valid's auc: 0.803951                                                                                                                                                   
[97]	valid's auc: 0.804447                                                                                                                                                   
[98]	valid's auc: 0.804044                                                                                                                                                   
[99]	valid's auc: 0.804412                                                                                                        

[141]	valid's auc: 0.809775                                                                                                                                                  
[142]	valid's auc: 0.810106                                                                                                                                                  
[143]	valid's auc: 0.810832                                                                                                                                                  
[144]	valid's auc: 0.810847                                                                                                                                                  
[145]	valid's auc: 0.811706                                                                                                                                                  
[146]	valid's auc: 0.811911                                                                                                       

[7]	valid's auc: 0.669524                                                                                                                                                    
[8]	valid's auc: 0.686197                                                                                                                                                    
[9]	valid's auc: 0.691936                                                                                                                                                    
[10]	valid's auc: 0.696278                                                                                                                                                   
[11]	valid's auc: 0.701959                                                                                                                                                   
[12]	valid's auc: 0.708064                                                                                                        

...

[267]	valid's auc: 0.80131                                                                                                                                                   
[268]	valid's auc: 0.801898                                                                                                                                                  
[269]	valid's auc: 0.802572                                                                                                                                                  
[270]	valid's auc: 0.802374                                                                                                                                                  
[271]	valid's auc: 0.802922                                                                                                                                                  
[272]	valid's auc: 0.803185                                                                                                       

[11]	valid's auc: 0.71989                                                                                                                                                    
[12]	valid's auc: 0.725867                                                                                                                                                   
[13]	valid's auc: 0.729753                                                                                                                                                   
[14]	valid's auc: 0.738794                                                                                                                                                   
[15]	valid's auc: 0.742705                                                                                                                                                   
[16]	valid's auc: 0.746479                                                                                                        

[58]	valid's auc: 0.804419                                                                                                                                                   
[59]	valid's auc: 0.804292                                                                                                                                                   
[60]	valid's auc: 0.807412                                                                                                                                                   
[61]	valid's auc: 0.805839                                                                                                                                                   
[62]	valid's auc: 0.80667                                                                                                                                                    
[63]	valid's auc: 0.804309                                                                                                        

[105]	valid's auc: 0.815049                                                                                                                                                  
[106]	valid's auc: 0.816115                                                                                                                                                  
[107]	valid's auc: 0.816125                                                                                                                                                  
[108]	valid's auc: 0.818026                                                                                                                                                  
[109]	valid's auc: 0.817683                                                                                                                                                  
[110]	valid's auc: 0.817678                                                                                                       

[152]	valid's auc: 0.821306                                                                                                                                                  
[153]	valid's auc: 0.820242                                                                                                                                                  
[154]	valid's auc: 0.821048                                                                                                                                                  
[155]	valid's auc: 0.8211                                                                                                                                                    
[156]	valid's auc: 0.821817                                                                                                                                                  
[157]	valid's auc: 0.82239                                                                                                        

In [13]:
results = hpo_utils.hyperopt2skopt(trials, SPACE)

best_auc = -1.0 * results.fun
best_params = results.x

# log metrics
print('Best Validation AUC: {}'.format(best_auc))
print('Best Params: {}'.format(best_params))

neptune.send_metric('validation auc', best_auc)

# log results
joblib.dump(trials, 'artifacts/hyperopt_trials.pkl')
joblib.dump(results, 'artifacts/hyperopt_results.pkl')
joblib.dump(SPACE, 'artifacts/hyperopt_space.pkl')

neptune.send_artifact('artifacts/hyperopt_trials.pkl')
neptune.send_artifact('artifacts/hyperopt_results.pkl')
neptune.send_artifact('artifacts/hyperopt_space.pkl')

# log runs
sk_utils.send_runs(results)
sk_utils.send_best_parameters(results)
sk_utils.send_plot_convergence(results, channel_name='diagnostics')
sk_utils.send_plot_evaluations(results, channel_name='diagnostics')

NameError: name 'hpo_utils' is not defined